# Electric Vehicle Adoption Trends - Data Exploration & Preprocessing

### 1. Import Required Libraries

In [57]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import warnings
warnings.filterwarnings("ignore")
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler

### 2. Load The Dataset

In [2]:
df = pd.read_csv('sample_data.csv')

### 3. Initial Data Exploration
#### 3.1 Data overview

In [3]:
df.shape

(15000, 17)

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15000 entries, 0 to 14999
Data columns (total 17 columns):
 #   Column                                             Non-Null Count  Dtype  
---  ------                                             --------------  -----  
 0   VIN (1-10)                                         15000 non-null  object 
 1   County                                             15000 non-null  object 
 2   City                                               15000 non-null  object 
 3   State                                              15000 non-null  object 
 4   Postal Code                                        15000 non-null  float64
 5   Model Year                                         15000 non-null  int64  
 6   Make                                               15000 non-null  object 
 7   Model                                              15000 non-null  object 
 8   Electric Vehicle Type                              15000 non-null  object 
 9   Clean 

**Insight:** 
- We have a 15,000-row dataset with 17 columns (mix of numeric & categorical).
- `VIN (1-10)` should be integer
- `Electric Range` & `Base MSRP`: 2 missing each.  
- `Legislative District`: 32 missing.  
- `Vehicle Location`: 1 missing.

In [5]:
df.head(2)

VIN (1-10) County     City State  Postal Code  Model Year        Make  \
0  JA4T5UA97P   King  Tukwila    WA      98188.0        2023  MITSUBISHI   
1  WVGUNPE28M   King   Duvall    WA      98019.0        2021  VOLKSWAGEN   

       Model                   Electric Vehicle Type  \
0  OUTLANDER  Plug-in Hybrid Electric Vehicle (PHEV)   
1       ID.4          Battery Electric Vehicle (BEV)   

   Clean Alternative Fuel Vehicle (CAFV) Eligibility  Electric Range  \
0            Clean Alternative Fuel Vehicle Eligible            38.0   
1  Eligibility unknown as battery range has not b...             0.0   

   Base MSRP  Legislative District  DOL Vehicle ID  \
0        0.0                  11.0       251088386   
1        0.0                  45.0       192403515   

              Vehicle Location                               Electric Utility  \
0  POINT (-122.29179 47.43473)  PUGET SOUND ENERGY INC||CITY OF TACOMA - (WA)   
1  POINT (-121.98609 47.74068)  PUGET SOUND ENERGY INC||CITY OF TACOMA - (WA)   

   2020 Census Tract  
0       5.303303e+10  
1       5.303303e+10

In [6]:
df.tail(2)

VIN (1-10)    County       City State  Postal Code  Model Year  Make  \
14998  1C4JJXR65P  Skamania  Stevenson    WA      98648.0        2023  JEEP   
14999  1C4RJXN6XR    Pierce     Tacoma    WA      98408.0        2024  JEEP   

          Model                   Electric Vehicle Type  \
14998  WRANGLER  Plug-in Hybrid Electric Vehicle (PHEV)   
14999  WRANGLER  Plug-in Hybrid Electric Vehicle (PHEV)   

      Clean Alternative Fuel Vehicle (CAFV) Eligibility  Electric Range  \
14998             Not eligible due to low battery range            21.0   
14999             Not eligible due to low battery range            21.0   

       Base MSRP  Legislative District  DOL Vehicle ID  \
14998        0.0                  14.0       260668397   
14999        0.0                  27.0       272922954   

                  Vehicle Location  \
14998  POINT (-121.88258 45.69417)   
14999  POINT (-122.44718 47.20144)   

                                        Electric Utility  2020 Census Tract  
14998  BONNEVILLE POWER ADMINISTRATION||PUD NO 1 OF S...       5.305995e+10  
14999  BONNEVILLE POWER ADMINISTRATION||CITY OF TACOM...       5.305306e+10

#### 3.2 Summary Statistics

In [7]:
pd.set_option('display.float_format', '{:.2f}'.format)
df.describe()

Postal Code  Model Year  Electric Range  Base MSRP  \
count     15000.00    15000.00        14998.00   14998.00   
mean      98182.86     2021.44           46.31     818.84   
std        2363.41        3.01           84.39    7101.53   
min        2842.00     2000.00            0.00       0.00   
25%       98052.00     2020.00            0.00       0.00   
50%       98133.00     2023.00            0.00       0.00   
75%       98374.00     2024.00           38.00       0.00   
max       99403.00     2025.00          337.00  110950.00   

       Legislative District  DOL Vehicle ID  2020 Census Tract  
count              14968.00        15000.00           15000.00  
mean                  28.81    235981705.94     52980075371.16  
std                   14.88     68340378.16      1539355467.40  
min                    1.00        10734.00      1101000900.00  
25%                   17.00    205561658.25     53033010200.00  
50%                   32.00    253273142.00     53033030404.00  
75%                   42.00    270199059.75     53053940011.00  
max                   49.00    478822942.00     53077940007.00

In [8]:
df.describe(include='O')

VIN (1-10) County     City  State   Make    Model  \
count        15000  15000    15000  15000  15000    15000   
unique        5370     63      354     15     38      145   
top     7SAYGDEEXP   King  Seattle     WA  TESLA  MODEL Y   
freq            89   7482     2373  14968   6516     3151   

                 Electric Vehicle Type  \
count                            15000   
unique                               2   
top     Battery Electric Vehicle (BEV)   
freq                             11968   

        Clean Alternative Fuel Vehicle (CAFV) Eligibility  \
count                                               15000   
unique                                                  3   
top     Eligibility unknown as battery range has not b...   
freq                                                 8950   

                   Vehicle Location  \
count                         14999   
unique                          448   
top     POINT (-122.13158 47.67858)   
freq                            372   

                                     Electric Utility  
count                                           15000  
unique                                             64  
top     PUGET SOUND ENERGY INC||CITY OF TACOMA - (WA)  
freq                                             5311

### 4. Data Cleaning
#### 4.1 Handle Missing & Duplicated Values 

In [9]:
df.isnull().sum()

VIN (1-10)                                            0
County                                                0
City                                                  0
State                                                 0
Postal Code                                           0
Model Year                                            0
Make                                                  0
Model                                                 0
Electric Vehicle Type                                 0
Clean Alternative Fuel Vehicle (CAFV) Eligibility     0
Electric Range                                        2
Base MSRP                                             2
Legislative District                                 32
DOL Vehicle ID                                        0
Vehicle Location                                      1
Electric Utility                                      0
2020 Census Tract                                     0
dtype: int64

In [10]:
df.dropna(inplace=True)

In [11]:
print(f'Duplicates: {df.duplicated().sum()}')

Duplicates: 0


#### 4.2 Drop Irrelevant Columns

In [12]:
df.drop(columns=['VIN (1-10)', 'Postal Code', 'Legislative District', 'DOL Vehicle ID'], inplace=True)

#### 4.3 Handle Outliers

In [13]:
for col in df[['Electric Range', 'Base MSRP']]:
    fig = px.box(df, x=col, title=f'Boxplot of {col}', color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400)
    fig.show()

In [14]:
df['Electric Range'] = df['Electric Range'].replace(0, np.nan)

In [15]:
df['Electric Range'].isna().sum()

8935

In [16]:
# Hierarchical imputation for 'Electric Range'
for cols in [
    ['Electric Vehicle Type', 'Make', 'Model', 'Model Year'],
    ['Electric Vehicle Type', 'Make', 'Model'],
    ['Electric Vehicle Type', 'Make'],
    ['Electric Vehicle Type']
]:
    df['Electric Range'] = df['Electric Range'].fillna(df.groupby(cols)['Electric Range'].transform('median'))
df['Electric Range'] = df['Electric Range'].fillna(df['Electric Range'].median())

In [17]:
df['Electric Range'].isna().sum()

0

In [18]:
px.box(df, x='Electric Range', title='Boxplot of Electric Range after Outlier Removal', color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400).show()

In [19]:
df['Base MSRP'] = df['Base MSRP'].replace(0, np.nan)

In [20]:
df['Base MSRP'].isna().sum()

14750

In [21]:
# Hierarchical imputation for 'Base MSRP'
for cols in [
    ['Electric Vehicle Type', 'Make', 'Model', 'Model Year'],
    ['Electric Vehicle Type', 'Make', 'Model'],
    ['Electric Vehicle Type', 'Make'],
    ['Electric Vehicle Type']
]:
    df['Base MSRP'] = df['Base MSRP'].fillna(df.groupby(cols)['Base MSRP'].transform('median'))
df['Base MSRP'] = df['Base MSRP'].fillna(df['Base MSRP'].median())

In [22]:
df['Base MSRP'].isna().sum()

0

In [23]:
px.box(df, x='Base MSRP', title='Boxplot of Base MSRP after Outlier Removal', color_discrete_sequence=px.colors.qualitative.Antique, 
       width=800, height=400).show()


### 5. Univariate Analysis
#### 5.1 Numeric Distributions

In [24]:
numeric_columns = ['Electric Range', 'Base MSRP', 'Model Year']
for col in numeric_columns:
    fig = px.histogram(df[col], x=col, title=f'Distribution of {col}', color_discrete_sequence= px.colors.qualitative.Antique, 
                       text_auto=True, nbins=10, width=800, height=400)
    fig.update_traces(marker=dict(line=dict(width=1, color='black')))
    fig.update_layout(title_x=0.5, xaxis_title=col, yaxis_title='Count', xaxis_tickangle=-45)
    fig.show()

**Insights:**
- `Electric Range` most EVs have ~200-250 miles range.
- `Base MSRP` shows high variance. 
- `Model Year` Most vehicles are recent models (2020-2025).

#### 5.2 Categorical Counts

In [25]:
fig = px.pie(df, names='Electric Vehicle Type', title='Distribution of Electric Vehicle Types', 
             color_discrete_sequence=px.colors.qualitative.Antique, 
             width=800, height=400)
fig.update_traces(textinfo='percent+label')
fig.update_layout(title_x=0.5)
fig.show()

**Insights:** Majority are BEVs have (79.8% of data) vs PHEVs account for (20.2%) .

In [26]:
# Top 10 Manufacturers distribution
make_percentage = df['Make'].value_counts(normalize=True).reset_index().rename(columns={'proportion': 'Percentage'})
make_percentage['Percentage'] = (make_percentage['Percentage'] * 100).round(2)
make_percentage.head(10)

Make  Percentage
0      TESLA       43.43
1  CHEVROLET        7.52
2     NISSAN        6.45
3       FORD        5.67
4        KIA        4.87
5     TOYOTA        3.80
6        BMW        3.76
7     RIVIAN        3.18
8    HYUNDAI        3.13
9       JEEP        2.67

In [27]:
fig = px.pie(make_percentage.head(10), names='Make', values='Percentage', title='Top 10 Manufacturers Distribution',
             color_discrete_sequence=px.colors.qualitative.Antique, 
             width=800, height=400, custom_data=['Percentage'], hole=0.3)
fig.update_traces(texttemplate='%{label}<br>%{customdata[0]}%',
    textinfo='text',
    hovertemplate='<b>%{label}</b><br>Percentage: %{customdata[0]}%'
)
fig.update_layout(title_x=0.5)
fig.show()

**Insights:** Top Manufacturers are TESLA (43.43% of vehicles), followed by CHEVROLET, NISSAN, and FORD.

In [28]:
px.pie(df, names='Clean Alternative Fuel Vehicle (CAFV) Eligibility', 
       title='Distribution of Clean Alternative Fuel Vehicle (CAFV) Eligibility',
         color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, hole=0.3).\
            update_traces(textinfo='percent+label').update_layout(title_x=0.5).show()

**Insights:** Majority (59.7%) have unknown eligibility due to unverified battery range.

### 6. Bivariate Analysis
#### 6.1 Electric Range vs. Model Year

In [29]:
fig = px.scatter(df, x='Model Year', y='Electric Range', title='Electric Rrange vs Model Year',
                 color_discrete_sequence=px.colors.qualitative.Antique,
                 width=800, height=400, marginal_x='histogram')
fig.update_traces(marker=dict(line=dict(width=1, color='black')))
fig.update_layout(title_x=0.5, xaxis_title='Model Year', yaxis_title='Electric Range', xaxis_tickangle=-45)
fig.show()

**Insight:** Newer models tend to have higher range, showing technology improvement over time.

#### 6.2 Electric Range by EV Type

In [30]:
EV_type_Range = df.groupby('Electric Vehicle Type')['Electric Range'].mean().reset_index().sort_values(by='Electric Range', ascending=False)
EV_type_Range = EV_type_Range.rename(columns={'Electric Range': 'Average Electric Range'})
EV_type_Range

Electric Vehicle Type  Average Electric Range
0          Battery Electric Vehicle (BEV)                  219.61
1  Plug-in Hybrid Electric Vehicle (PHEV)                   30.94

In [31]:
fig = px.bar(EV_type_Range, x='Electric Vehicle Type', y='Average Electric Range',
             title='Average Electric Range by Electric Vehicle Type',
                color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, text_auto=True)
fig.update_traces(marker=dict(line=dict(width=1, color='black')))
fig.update_layout(title_x=0.5, xaxis_title='Electric Vehicle Type', yaxis_title='Average Electric Range')
fig.show()

In [32]:
fig = px.box(df, y='Electric Vehicle Type', x='Electric Range', title='Electric Range by Electric Vehicle Type',
            width=800, height=400,
            color_discrete_sequence=px.colors.qualitative.Antique)
fig.update_traces(marker=dict(line=dict(width=1, color='black')))
fig.update_layout(title_x=0.5, yaxis_title='Electric Vehicle Type', xaxis_title='Electric Range')
fig.show()

**Insight:** BEVs generally have high Electric Range (average range ~219 miles) compared to PHEVs have ( average range ~31 miles)

#### 6.3 Electric Range by Make

In [33]:
# Top 10 Manufacturers by Electric Range
ER_Make = df.groupby('Make')['Electric Range'].mean().reset_index().sort_values(by='Electric Range', ascending=False)
ER_Make = ER_Make.rename(columns={'Electric Range': 'Average Electric Range'})
top_10_make_ER = ER_Make.head(10).round(2)
top_10_make_ER


Make  Average Electric Range
34        TESLA                  259.38
0         ACURA                  238.00
12          GMC                  238.00
11      GENESIS                  238.00
22        LUCID                  238.00
31  ROLLS-ROYCE                  238.00
30       RIVIAN                  238.00
15       JAGUAR                  234.00
28     POLESTAR                  233.00
9        FISKER                  225.19

In [34]:
fig = px.bar(top_10_make_ER, x='Make', y='Average Electric Range',
             title='Top 10 Manufacturers by Average Electric Range',
                color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, text_auto=True)
fig.update_traces(marker=dict(line=dict(width=1, color='black')))
fig.update_layout(title_x=0.5, xaxis_title='Make', yaxis_title='Average Electric Range (miles)')
fig.show()

**Insights**: Top Manufacturers by Average Electric Range are TESLA (~259 miles),  followed by ACURA, GMC, and GENESIS.

#### 6.4 Base MSRP by EV Type

In [35]:
EV_type_MSRP = df.groupby('Electric Vehicle Type')['Base MSRP'].mean().reset_index().sort_values(by='Base MSRP', ascending=False)
EV_type_MSRP = EV_type_MSRP.rename(columns={'Base MSRP': 'Average Base MSRP'})
EV_type_MSRP

Electric Vehicle Type  Average Base MSRP
0          Battery Electric Vehicle (BEV)           68250.93
1  Plug-in Hybrid Electric Vehicle (PHEV)           52538.15

In [36]:
fig = px.bar(EV_type_MSRP, x='Electric Vehicle Type', y='Average Base MSRP', title='Average Base MSRP by Electric Vehicle Type',
                color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, text_auto=True)
fig.update_traces(marker=dict(line=dict(width=1, color='black')))
fig.update_layout(title_x=0.5, xaxis_title='Electric Vehicle Type', yaxis_title='Average Base MSRP')
fig.show()

In [37]:
fig = px.box(df, x='Base MSRP', y='Electric Vehicle Type',title='Base MSRP by EV Type', 
             color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400)
fig.update_traces(marker=dict(line=dict(width=1, color='black')))
fig.update_layout(title_x=0.5, xaxis_title='Base MSRP', yaxis_title='Electric Vehicle Type')
fig.show()

**Insight:** BEVs generally have higher Base MSRP compared to PHEVs.

### 7. Geographical Distribution

In [38]:
# Top 10 Counties Adopting Electric Vehicles
country_adoption_percentage = df['County'].value_counts(normalize=True).reset_index().rename(columns={'proportion': 'Percentage'})
country_adoption_percentage['Percentage'] = (country_adoption_percentage['Percentage'] * 100).round(2)
country_adoption_percentage.head(10)

County  Percentage
0       King       49.99
1  Snohomish       12.59
2     Pierce        8.14
3      Clark        5.81
4   Thurston        3.78
5     Kitsap        3.51
6    Spokane        2.91
7    Whatcom        2.45
8     Skagit        1.18
9     Benton        1.18

In [39]:
fig = px.pie(country_adoption_percentage.head(5), names='County', values='Percentage', title='Top 5 Counties Adopting Electric Vehicles',
       color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, hole=0.3, custom_data=['Percentage'])
fig.update_traces(texttemplate='%{label}<br>%{customdata[0]}%',
    textinfo='text',
    hovertemplate='<b>%{label}</b><br>Percentage: %{customdata[0]}%'
)
fig.update_layout(title_x=0.5)
fig.show()

**Insight:** King County (49.9%) leads adoption.

In [40]:
df[['Lon', 'Lat']] = df['Vehicle Location'].str.extract(r'\((-?\d+\.\d+) (-?\d+\.\d+)').astype(float)
df.head(1)

County     City State  Model Year        Make      Model  \
0   King  Tukwila    WA        2023  MITSUBISHI  OUTLANDER   

                    Electric Vehicle Type  \
0  Plug-in Hybrid Electric Vehicle (PHEV)   

  Clean Alternative Fuel Vehicle (CAFV) Eligibility  Electric Range  \
0           Clean Alternative Fuel Vehicle Eligible           38.00   

   Base MSRP             Vehicle Location  \
0   52650.00  POINT (-122.29179 47.43473)   

                                Electric Utility  2020 Census Tract     Lon  \
0  PUGET SOUND ENERGY INC||CITY OF TACOMA - (WA)     53033028200.00 -122.29   

    Lat  
0 47.43

In [41]:
EV_geo_dist = df.groupby(['Lon', 'Lat','City', 'Make'])['Electric Vehicle Type'].value_counts().\
                            reset_index(name='Count').sort_values(by='Count', ascending=False)
EV_geo_dist.head(10)

Lon   Lat           City   Make           Electric Vehicle Type  \
3438 -122.13 47.68        Redmond  TESLA  Battery Electric Vehicle (BEV)   
2952 -122.21 47.68       Kirkland  TESLA  Battery Electric Vehicle (BEV)   
2901 -122.21 47.83        Bothell  TESLA  Battery Electric Vehicle (BEV)   
3484 -122.12 47.56       Bellevue  TESLA  Battery Electric Vehicle (BEV)   
3770 -122.02 47.60      Sammamish  TESLA  Battery Electric Vehicle (BEV)   
3093 -122.19 47.61       Bellevue  TESLA  Battery Electric Vehicle (BEV)   
3156 -122.18 47.80        Bothell  TESLA  Battery Electric Vehicle (BEV)   
3673 -122.04 47.61      Sammamish  TESLA  Battery Electric Vehicle (BEV)   
2870 -122.21 47.58  Mercer Island  TESLA  Battery Electric Vehicle (BEV)   
3388 -122.16 47.75    Woodinville  TESLA  Battery Electric Vehicle (BEV)   

      Count  
3438    206  
2952    159  
2901    145  
3484    135  
3770    114  
3093    113  
3156    102  
3673     92  
2870     92  
3388     91

In [42]:
fig = px.scatter_map(EV_geo_dist, lat='Lat', lon='Lon', hover_name='City', hover_data=['Make'],
                    color='Electric Vehicle Type', size='Count',
                    size_max=20, opacity=0.7,
                    title='Vehicle Locations', color_discrete_sequence=px.colors.qualitative.Antique, 
                    height=400, zoom=5, center=dict(lat=47.5, lon=-122.5))
fig.show()

**Insight:** Strong concentration in urban areas (Seattle-Bellevue-Redmond)

### 8. Multivariate Analysis

In [43]:
eligibility_counts = df.groupby(['Make','Model Year','Clean Alternative Fuel Vehicle (CAFV) Eligibility'])\
                                ['Clean Alternative Fuel Vehicle (CAFV) Eligibility'].count().reset_index(name='Count')\
                                .sort_values(by='Count', ascending=False)
eligibility_counts

Make  Model Year  \
288        TESLA        2023   
289        TESLA        2024   
287        TESLA        2022   
286        TESLA        2021   
283        TESLA        2018   
..           ...         ...   
89          FORD        2015   
84          FORD        2000   
82        FISKER        2012   
169   LAND ROVER        2024   
167  LAMBORGHINI        2024   

     Clean Alternative Fuel Vehicle (CAFV) Eligibility  Count  
288  Eligibility unknown as battery range has not b...   1762  
289  Eligibility unknown as battery range has not b...   1052  
287  Eligibility unknown as battery range has not b...    876  
286  Eligibility unknown as battery range has not b...    717  
283            Clean Alternative Fuel Vehicle Eligible    537  
..                                                 ...    ...  
89             Clean Alternative Fuel Vehicle Eligible      1  
84             Clean Alternative Fuel Vehicle Eligible      1  
82             Clean Alternative Fuel Vehicle Eligible      1  
169            Clean Alternative Fuel Vehicle Eligible      1  
167              Not eligible due to low battery range      1  

[336 rows x 4 columns]

In [44]:
fig = px.bar(eligibility_counts, x='Make', y='Count', color='Clean Alternative Fuel Vehicle (CAFV) Eligibility',
             title='CAFV Eligibility by Make and Model Year', color_discrete_sequence=px.colors.qualitative.Antique,
             barmode='group', hover_data=['Model Year'])
fig.update_traces(marker=dict(line=dict(width=1, color='black')))
fig.update_layout(title_x=0.5, xaxis_title='Make', yaxis_title='Count', xaxis_tickangle=-45)
fig.show()

**Insight:** Tesla dominates in Clean Alternative Fuel Vehicle eligibility.

In [45]:
corr = df[numeric_columns].corr()
corr

Electric Range  Base MSRP  Model Year
Electric Range            1.00       0.48        0.27
Base MSRP                 0.48       1.00        0.06
Model Year                0.27       0.06        1.00

In [46]:
fig = px.imshow(corr, text_auto=True, color_continuous_scale=px.colors.sequential.Brwnyl, 
                title='Correlation Matrix',
                color_continuous_midpoint=0, width=800, height=500)
fig.show()

**Insight:** Electric Range shows moderate positive correlation with Base MSRP, and Model Year

### 9. Streamlit Dashboard

In [47]:
%%writefile Electric_Vehicle_Adoption_Dashboard.py
# Streamlit Dashboard

import streamlit as st
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# 1. Page Configuration
st.set_page_config(
    page_title='EV Adoption Dashboard',
    layout='wide',
    initial_sidebar_state='expanded',
    page_icon='🚗',
)

# Title
st.title('🚗 Electric Vehicle Adoption Trends')
st.markdown('---')

# 2. Load Original Data (Uncleaned)
@st.cache_data
def load_original_data():
    df = pd.read_csv('sample_data.csv')
    df.columns = [c.strip().lower().replace(' ', '_') for c in df.columns]
    return df

df_orig = load_original_data()

# 3. Create Cleaned DataFrame
@st.cache_data
def clean_data(df):
    df_clean = df.copy()
    # Drop duplicates
    df_clean.drop_duplicates(inplace=True)
    # Drop rows missing critical values
    df_clean.dropna(inplace=True)
    # Drop irrelevant columns
    drop_cols = ['vin_(1-10)', 'postal_code', 'dol_vehicle_id', 'legislative_district']
    df_clean.drop(columns=drop_cols, errors='ignore', inplace=True)
    # Remove outliers via hierarchical median imputation
    for col in ['electric_range', 'base_msrp']:
        # Replace 0 with NaN
        df_clean[col] = df_clean[col].replace(0, np.nan)
        # Hierarchical imputation
        for cols in [
        ['electric_vehicle_type', 'make', 'model', 'model_year'],
        ['electric_vehicle_type', 'make', 'model'],
        ['electric_vehicle_type', 'make'],
        ['electric_vehicle_type']
        ]:
            df_clean[col] = df_clean[col].fillna(df_clean.groupby(cols)[col].transform('median'))
        df_clean[col] = df_clean[col].fillna(df_clean[col].median())

    return df_clean

df_clean = clean_data(df_orig)

# 4. Sidebar: Page Navigation
st.sidebar.title('📊 Navigation')
st.sidebar.markdown('**Select a page to explore the data:**')
page = st.sidebar.radio(
    'Select Page', ['Data Overview', 'Cleaned Data', 'Charts']
)
st.sidebar.markdown('---')
# 5. Filters (for pages 2 & 3)
# Show filters only for Cleaned Data & Charts pages
def apply_filters(df_clean):
    # Sidebar - Professional Filters
    st.sidebar.title('🔎 Filters')
    # Multi-select: Make
    make_options = df_clean['make'].unique().tolist()
    selected_makes = st.sidebar.multiselect('Brand', make_options, default=make_options[:3])
    
    # Slider: Model Year
    year_min, year_max = int(df_clean['model_year'].min()), int(df_clean['model_year'].max())
    selected_year = st.sidebar.slider('Model Year', year_min, year_max, (year_min, year_max))

    # Multi-select: EV Type
    type_options = df_clean['electric_vehicle_type'].unique().tolist()
    selected_types = st.sidebar.multiselect('Electric Vehicle Type', type_options, default=type_options)

    # Slider: Range
    range_min, range_max = int(df_clean['electric_range'].min()), int(df_clean['electric_range'].max())
    selected_range = st.sidebar.slider('Electric Range (miles)', range_min, range_max, (range_min, range_max))

    # Multi-select: Electric Utility
    cafv_opts = [
        'Clean Alternative Fuel Vehicle Eligible',
        'Eligibility unknown as battery range has not been researched',
        'Not eligible due to low battery range'
    ]
    cafv_sel = st.sidebar.multiselect('CAFV Eligibility', cafv_opts, default=cafv_opts)

    # Apply Filters
    df_filtered = df_clean[
        df_clean['make'].isin(selected_makes) &
        df_clean['electric_vehicle_type'].isin(selected_types) &
        df_clean['model_year'].between(*selected_year) &
        (df_clean['electric_range'].between(*selected_range)) &
        df_clean['clean_alternative_fuel_vehicle_(cafv)_eligibility'].isin(cafv_sel)
    ]
    
    return df_filtered

# 6. Page Content
info_text = """
This dataset shows the Battery Electric Vehicles (BEVs) and Plug-in Hybrid Electric Vehicles (PHEVs) that are currently registered through Washington State Department of Licensing (DOL).
"""
notes_text = """
#### Notes

1. **Battery Electric Vehicle (BEV)**: An all-electric vehicle using one or more batteries to store the electrical energy that powers the motor and is charged by plugging the vehicle into an electric power source.

    **Plug-in Hybrid Electric Vehicle (PHEV)**: A vehicle that uses one or more batteries to power an electric motor, and also uses another fuel (e.g., gasoline or diesel) to power an internal combustion engine or other propulsion source; and is charged by plugging the vehicle into an electric power source.

2. **CAFV Eligibility**: Clean Alternative Fuel Vehicle (CAFV) Eligibility is based on the fuel requirement and electric-only range requirement as outlined in RCW 82.08.809 and RCW 82.12.809. Sales or leases must occur on or after 8/1/2019 and meet purchase price requirements to qualify for exemptions.

3. **Electric Range Note**: Range is no longer maintained for BEVs with range over 30 miles. Zero (0) indicates unknown or unresearched range.
"""

if page == 'Data Overview':
    st.header('📋 Data Overview')

    st.markdown(info_text)
    st.markdown(notes_text)
    
    st.subheader('Dataset Snapshot')
    st.write(df_orig.head(6))

    st.subheader('Columns Summary')
    col_defs = pd.DataFrame({
        'Column Name': [
            'VIN (1-10)', 
            'County . City . State',
            'Portal Code',
            'Model Year',
            'Make . Model',
            'Electric Vehicle Type',
            'CAFV Eligibility',
            'Electric Range',
            'Base MSRP',
            'Legislative District',
            'DOL Vehicle ID',
            'Vehicle Location',
            'Electric Utility',
            '2000 Census Track'
        ],
        'Type': [
            'object', 'object', 'float64', 'int64', 'object', 'object', 'object',
            'float64', 'float64', 'float64', 'int64', 'object', 'object', 'float64'
        ],
        'Description': [
            'Likely anonymized ID; good candidate for drop',
            'Location info for geographic trends',
            'Can help group by region might convert to int',
            'Useful for age analysis',
            'Brand and vehicle details',
            'BEV, PHEV, etc. - critical for filtering groups',
            'Whether vehicle qualifies for fuel programs',
            'Key metric - prediction target',
            'Price - strong predictor',
            'Possibly useful for policy insight',
            'Internal - drop candidate',
            '(lat, lon) as string - useful for geoplots',
            'Can be linked with infrastructure info',
            'Geographic demographic mapping'
        ]
    })

    st.dataframe(col_defs, 
                 column_order=['Column Name', 'Type', 'Description'],
                 hide_index=True,
                 use_container_width=True)


    st.subheader('Info')
    
    st.write(f'**Rows:** {df_orig.shape[0]}  \ **Columns:** {df_orig.shape[1]}  \ **Each row represents a:** Vehicle')
    st.write(f'**Memory Usage:** {df_orig.memory_usage().sum() / 1024 ** 2:.2f} MB')

    st.subheader('Statistical Summary')
    st.write(df_orig.describe())
    st.write(df_orig.describe(include='O'))

    st.subheader('Missing & Duplicate Values')
    st.write('Missing Values Of Each Column:')
    st.dataframe(pd.DataFrame(df_orig.isnull().sum()).T, hide_index=True, use_container_width=True)
    st.write(f'Duplicate Rows: {df_orig.duplicated().sum()}')

    fig = px.pie(df_orig, names='clean_alternative_fuel_vehicle_(cafv)_eligibility', 
                title='Distribution of Clean Alternative Fuel Vehicle (CAFV) Eligibility',
                color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, hole=0.3)
    fig.update_traces(textinfo='percent+label').update_layout(title_x=0.5)
    st.plotly_chart(fig, use_container_width=True)

elif page == 'Cleaned Data':
    cleaning_text = """
    #### Cleaning Steps:

    1. Drop duplicates.

    2. Drop rows missing critical values.

    3. Drop irrelevant columns.

    4. Remove outliers via hierarchical median imputation:
        
        4.1 Replace 0 with NaN.
        
        4.2 Hierarchical imputation.
    """
    st.header('🧹 Data Cleaning')
    st.markdown(cleaning_text)
    st.markdown('---')
    st.subheader('Filtered Data Snapshot')
    df_filtered = apply_filters(df_clean)
    st.write(df_filtered.head(10))
    st.subheader('Filtered Data Shape')
    st.write(df_filtered.shape)
    st.write(f'**Rows:** {df_filtered.shape[0]}  \ **Columns:** {df_filtered.shape[1]}  \ **Each row represents a:** Vehicle')

elif page == 'Charts':
    st.header('📊 Charts of Filtered and Cleaned Data')
    df_filtered = apply_filters(df_clean)
    tab1, tab2, tab3, tab4 = st.tabs(['Univariate Analysis', 'Bivariate Analysis', 'Geographical Distribution', 'Multivariate Analysis'])

    with tab1:
        st.subheader('Univariate Analysis')
        # Histogram
        for col in ['electric_range', 'base_msrp', 'model_year']:
            fig1 = px.histogram(df_filtered[col], x=col, title=f'Distribution of {col}', 
                                color_discrete_sequence= px.colors.qualitative.Antique,
                                text_auto=True, 
                                nbins=10, width=800, height=400)
            fig1.update_traces(marker=dict(line=dict(width=1, color='black')))
            fig1.update_layout(title_x=0.5, xaxis_title=col, yaxis_title='Count', xaxis_tickangle=-45)
            st.plotly_chart(fig1, use_container_width=True)

        fig2 = px.histogram(df_filtered['make'].value_counts().reset_index(), x='count' ,y='make', title='Distribution of Make',
                            text_auto=True, color_discrete_sequence=px.colors.qualitative.Antique, 
                            width=800, height=400)
        fig2.update_traces(marker=dict(line=dict(width=1, color='black')))
        fig2.update_layout(title_x=0.5, yaxis_title='Make', xaxis_title='Count', xaxis_tickangle=-45)
        st.plotly_chart(fig2, use_container_width=True)

        # Pie
        fig3 = px.pie(df_filtered, names='electric_vehicle_type', title='Distribution of Electric Vehicle Types', 
                    color_discrete_sequence=px.colors.qualitative.Antique, 
                    width=800, height=400, hole=0.3)
        fig3.update_traces(textinfo='percent+label')
        fig3.update_layout(title_x=0.5)
        st.plotly_chart(fig3, use_container_width=True)


    with tab2:
        st.subheader('Bivariate Analysis')
        # Scatter
        fig4 = px.scatter(df_filtered, x='model_year', y='electric_range', title='Electric Rrange vs Model Year',
                 color_discrete_sequence=px.colors.qualitative.Antique,
                 width=800, height=400, marginal_x='histogram')
        fig4.update_traces(marker=dict(line=dict(width=1, color='black')))
        fig4.update_layout(title_x=0.5, xaxis_title='Model Year', yaxis_title='Electric Range', xaxis_tickangle=-45)
        st.plotly_chart(fig4, use_container_width=True)

        # Bar Chart
        make_range = df_filtered.groupby('make')['electric_range'].mean()\
                .reset_index().sort_values(by='electric_range', ascending=False)
        make_range = make_range.rename(columns={'electric_range': 'Average Electric Range'})

        fig5 = px.bar(make_range, x='make', y='Average Electric Range', title='Average Electric Range by Make',
                color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, text_auto=True)
        fig5.update_traces(marker=dict(line=dict(width=1, color='black')))
        fig5.update_layout(title_x=0.5, xaxis_title='Make', yaxis_title='Average Electric Range')
        st.plotly_chart(fig5, use_container_width=True)

        EV_type_Range = df_filtered.groupby('electric_vehicle_type')['electric_range'].mean()\
                .reset_index().sort_values(by='electric_range', ascending=False)
        EV_type_Range = EV_type_Range.rename(columns={'electric_range': 'Average Electric Range'})

        fig6 = px.bar(EV_type_Range, x='electric_vehicle_type', y='Average Electric Range', title='Average Electric Range by Electric Vehicle Type',
                color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, text_auto=True)
        fig6.update_traces(marker=dict(line=dict(width=1, color='black')))
        fig6.update_layout(title_x=0.5, xaxis_title='Electric Vehicle Type', yaxis_title='Average Electric Range')
        st.plotly_chart(fig6, use_container_width=True)

        EV_type_MSRP = df_filtered.groupby('electric_vehicle_type')['base_msrp'].mean().\
                    reset_index().sort_values(by='base_msrp', ascending=False)
        EV_type_MSRP = EV_type_MSRP.rename(columns={'base_msrp': 'Average Base MSRP'})

        fig7 = px.bar(EV_type_MSRP, x='electric_vehicle_type', y='Average Base MSRP', title='Average Base MSRP by Electric Vehicle Type',
                color_discrete_sequence=px.colors.qualitative.Antique, width=800, height=400, text_auto=True)
        fig7.update_traces(marker=dict(line=dict(width=1, color='black')))
        fig7.update_layout(title_x=0.5, xaxis_title='Electric Vehicle Type', yaxis_title='Average Base MSRP')
        st.plotly_chart(fig7, use_container_width=True)


    with tab3:
        st.subheader('Geographical Distribution')
        # Scatter Map
        df_filtered[['lon', 'lat']] = df_filtered['vehicle_location'].str.extract(r'\((-?\d+\.\d+) (-?\d+\.\d+)\)').astype(float)
        EV_geo_dist = df_filtered.groupby(['lon', 'lat','city', 'make'])['electric_vehicle_type']\
                        .value_counts().reset_index(name='count')\
                    .sort_values(by='count', ascending=False)

        fig8 = px.scatter_map(EV_geo_dist ,lat='lat', lon='lon', hover_name='city', hover_data=['make'],
                    color='electric_vehicle_type', size='count',
                    size_max=20, opacity=0.7,
                    title='Vehicle Locations', color_discrete_sequence=px.colors.qualitative.Antique, 
                    zoom=5, center=dict(lat=47.5, lon=-122.5))
        st.plotly_chart(fig8, use_container_width=True)

    with tab4:
        st.subheader('Multivariate Analysis')
        # Correlation Matrix
        corr = df_filtered[['electric_range', 'base_msrp', 'model_year']].corr()
        fig9 = px.imshow(corr, text_auto=True, color_continuous_scale=px.colors.sequential.Brwnyl, 
                title='Correlation Matrix',
                color_continuous_midpoint=0, width=800, height=500)
        st.plotly_chart(fig9, use_container_width=True)

        # Bar Chart
        eligibility_counts = df_filtered.groupby(['make','model_year','clean_alternative_fuel_vehicle_(cafv)_eligibility'])\
                                ['clean_alternative_fuel_vehicle_(cafv)_eligibility'].count().reset_index(name='count')\
                                .sort_values(by='count', ascending=False)
        fig10 = px.bar(eligibility_counts, x='make', y='count', color='clean_alternative_fuel_vehicle_(cafv)_eligibility',
             title='CAFV Eligibility by Make and Model Year', color_discrete_sequence=px.colors.qualitative.Antique,
             barmode='group', hover_data=['model_year'])
        fig10.update_traces(marker=dict(line=dict(width=1, color='black')))
        fig10.update_layout(title_x=0.5, xaxis_title='Make', yaxis_title='Count', xaxis_tickangle=-45)
        st.plotly_chart(fig10, use_container_width=True)

# 5. Footer
st.sidebar.markdown('---')
st.sidebar.markdown('**Data Source:** Washington State EV Registration Data')
st.sidebar.markdown('**Created by:** Amr Taghyan')


Overwriting Electric_Vehicle_Adoption_Dashboard.py


In [ ]:
# ! streamlit run Electric_Vehicle_Adoption_Dashboard.py

^C


### 10. Data Preprocessing


In [49]:
# Save cleaned data
df_cleaned = df.to_csv('cleaned_data.csv', index=False)

In [50]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 14965 entries, 0 to 14999
Data columns (total 15 columns):
 #   Column                                             Non-Null Count  Dtype  
---  ------                                             --------------  -----  
 0   County                                             14965 non-null  object 
 1   City                                               14965 non-null  object 
 2   State                                              14965 non-null  object 
 3   Model Year                                         14965 non-null  int64  
 4   Make                                               14965 non-null  object 
 5   Model                                              14965 non-null  object 
 6   Electric Vehicle Type                              14965 non-null  object 
 7   Clean Alternative Fuel Vehicle (CAFV) Eligibility  14965 non-null  object 
 8   Electric Range                                     14965 non-null  float64
 9   Base MSRP  

In [51]:
df_preprocess = df.copy()
df_preprocess.head(1)

County     City State  Model Year        Make      Model  \
0   King  Tukwila    WA        2023  MITSUBISHI  OUTLANDER   

                    Electric Vehicle Type  \
0  Plug-in Hybrid Electric Vehicle (PHEV)   

  Clean Alternative Fuel Vehicle (CAFV) Eligibility  Electric Range  \
0           Clean Alternative Fuel Vehicle Eligible           38.00   

   Base MSRP             Vehicle Location  \
0   52650.00  POINT (-122.29179 47.43473)   

                                Electric Utility  2020 Census Tract     Lon  \
0  PUGET SOUND ENERGY INC||CITY OF TACOMA - (WA)     53033028200.00 -122.29   

    Lat  
0 47.43

In [52]:
df_preprocess.drop(columns=['County', 'City', 'State', 'Vehicle Location', 'Electric Utility' ,'2020 Census Tract', 'Lon', 'Lat'], inplace=True)

#### 10.1 Handle Categorical Data

In [53]:
df_preprocess.head(2)

Model Year        Make      Model                   Electric Vehicle Type  \
0        2023  MITSUBISHI  OUTLANDER  Plug-in Hybrid Electric Vehicle (PHEV)   
1        2021  VOLKSWAGEN       ID.4          Battery Electric Vehicle (BEV)   

   Clean Alternative Fuel Vehicle (CAFV) Eligibility  Electric Range  \
0            Clean Alternative Fuel Vehicle Eligible           38.00   
1  Eligibility unknown as battery range has not b...          125.00   

   Base MSRP  
0   52650.00  
1   69900.00

In [54]:
# one-hot encoding for categorical variables
df_encoded = pd.get_dummies(df_preprocess, drop_first=True, dtype=int)
df_encoded.head(5)

Model Year  Electric Range  Base MSRP  Make_ALFA ROMEO  Make_AUDI  \
0        2023           38.00   52650.00                0          0   
1        2021          125.00   69900.00                0          0   
2        2023          220.00   69900.00                0          0   
3        2024          238.00   69900.00                0          0   
4        2022           76.00   69900.00                0          0   

   Make_BMW  Make_CADILLAC  Make_CHEVROLET  Make_CHRYSLER  Make_DODGE  ...  \
0         0              0               0              0           0  ...   
1         0              0               0              0           0  ...   
2         0              0               0              0           0  ...   
3         0              1               0              0           0  ...   
4         0              0               0              0           0  ...   

   Model_WRANGLER  Model_X3  Model_X5  Model_XC40  Model_XC60  Model_XC90  \
0               0         0         0           0           0           0   
1               0         0         0           0           0           0   
2               0         0         0           0           0           0   
3               0         0         0           0           0           0   
4               0         0         0           0           0           0   

   Model_ZDX  Electric Vehicle Type_Plug-in Hybrid Electric Vehicle (PHEV)  \
0          0                                                  1              
1          0                                                  0              
2          0                                                  0              
3          0                                                  0              
4          0                                                  0              

   Clean Alternative Fuel Vehicle (CAFV) Eligibility_Eligibility unknown as battery range has not been researched  \
0                                                  0                                                                
1                                                  1                                                                
2                                                  1                                                                
3                                                  1                                                                
4                                                  1                                                                

   Clean Alternative Fuel Vehicle (CAFV) Eligibility_Not eligible due to low battery range  
0                                                  0                                        
1                                                  0                                        
2                                                  0                                        
3                                                  0                                        
4                                                  0                                        

[5 rows x 187 columns]

#### 10.2 Determine Features and Target variables

In [55]:
X = df_encoded.drop(columns=['Electric Range']) # features
y = df_encoded['Electric Range'] # target variable

#### 10.3 Splitting Data into Training and Testing sets

In [56]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

#### 10.4 Scaling

In [58]:
# RobustScaler for scaling
R_scaler = RobustScaler()
X_train_R_scaled = R_scaler.fit_transform(X_train)
X_test_R_scaled = R_scaler.transform(X_test)

In [59]:
X_train_R_scaled = pd.DataFrame(X_train_R_scaled, columns=X_train.columns)
X_test_R_scaled = pd.DataFrame(X_test_R_scaled, columns=X_test.columns)

In [60]:
X_train_R_scaled.head(1)

Model Year  Base MSRP  Make_ALFA ROMEO  Make_AUDI  Make_BMW  Make_CADILLAC  \
0       -1.75   -4950.00             0.00       0.00      0.00           0.00   

   Make_CHEVROLET  Make_CHRYSLER  Make_DODGE  Make_FIAT  ...  Model_WRANGLER  \
0            0.00           0.00        0.00       0.00  ...            0.00   

   Model_X3  Model_X5  Model_XC40  Model_XC60  Model_XC90  Model_ZDX  \
0      0.00      0.00        0.00        0.00        1.00       0.00   

   Electric Vehicle Type_Plug-in Hybrid Electric Vehicle (PHEV)  \
0                                               1.00              

   Clean Alternative Fuel Vehicle (CAFV) Eligibility_Eligibility unknown as battery range has not been researched  \
0                                              -1.00                                                                

   Clean Alternative Fuel Vehicle (CAFV) Eligibility_Not eligible due to low battery range  
0                                               1.00                                        

[1 rows x 186 columns]

In [61]:
X_test_R_scaled.head(1)

Model Year  Base MSRP  Make_ALFA ROMEO  Make_AUDI  Make_BMW  Make_CADILLAC  \
0        0.25       0.00             0.00       0.00      0.00           0.00   

   Make_CHEVROLET  Make_CHRYSLER  Make_DODGE  Make_FIAT  ...  Model_WRANGLER  \
0            0.00           0.00        0.00       0.00  ...            0.00   

   Model_X3  Model_X5  Model_XC40  Model_XC60  Model_XC90  Model_ZDX  \
0      0.00      0.00        0.00        0.00        0.00       0.00   

   Electric Vehicle Type_Plug-in Hybrid Electric Vehicle (PHEV)  \
0                                               0.00              

   Clean Alternative Fuel Vehicle (CAFV) Eligibility_Eligibility unknown as battery range has not been researched  \
0                                               0.00                                                                

   Clean Alternative Fuel Vehicle (CAFV) Eligibility_Not eligible due to low battery range  
0                                               0.00                                        

[1 rows x 186 columns]